# Eager Few Shot Object Detection Colab

Welcome to the Eager Few Shot Object Detection Colab --- in this colab we demonstrate fine tuning of a (TF2 friendly) RetinaNet architecture on very few examples of a novel class after initializing from a pre-trained COCO checkpoint.
Training runs in eager mode.

Estimated time to run through this colab (with GPU): < 5 minutes.

## Imports

In [1]:
import matplotlib
import matplotlib.pyplot as plt

import os
import random
import io
import imageio
import glob
import scipy.misc
import numpy as np
from six import BytesIO
from PIL import Image, ImageDraw, ImageFont
from IPython.display import display, Javascript
from IPython.display import Image as IPyImage

import tensorflow as tf
physical_devices = tf.config.list_physical_devices('GPU') 
tf.config.experimental.set_memory_growth(physical_devices[0], True)

from object_detection.utils import label_map_util
from object_detection.utils import config_util
from object_detection.utils import visualization_utils as viz_utils
#from object_detection.utils import colab_utils
from object_detection.builders import model_builder

%matplotlib inline

# Utilities

In [2]:
def load_image_into_numpy_array(path):
  """Load an image from file into a numpy array.

  Puts image into numpy array to feed into tensorflow graph.
  Note that by convention we put it into a numpy array with shape
  (height, width, channels), where channels=3 for RGB.

  Args:
    path: a file path.

  Returns:
    uint8 numpy array with shape (img_height, img_width, 3)
  """
  img_data = tf.io.gfile.GFile(path, 'rb').read()
  image = Image.open(BytesIO(img_data))
  (im_width, im_height) = image.size
  return np.array(image.getdata()).reshape(
      (im_height, im_width, 3)).astype(np.uint8)


def plot_detections(image_np,
                    boxes,
                    classes,
                    scores,
                    category_index,
                    figsize=(12, 16),
                    image_name=None):
  """Wrapper function to visualize detections.

  Args:
    image_np: uint8 numpy array with shape (img_height, img_width, 3)
    boxes: a numpy array of shape [N, 4]
    classes: a numpy array of shape [N]. Note that class indices are 1-based,
      and match the keys in the label map.
    scores: a numpy array of shape [N] or None.  If scores=None, then
      this function assumes that the boxes to be plotted are groundtruth
      boxes and plot all boxes as black with no classes or scores.
    category_index: a dict containing category dictionaries (each holding
      category index `id` and category name `name`) keyed by category indices.
    figsize: size for the figure.
    image_name: a name for the image file.
  """
  image_np_with_annotations = image_np.copy()
  viz_utils.visualize_boxes_and_labels_on_image_array(
      image_np_with_annotations,
      boxes,
      classes,
      scores,
      category_index,
      use_normalized_coordinates=True,
      min_score_thresh=0.8)
  if image_name:
    plt.imsave(image_name, image_np_with_annotations)
  else:
    plt.imshow(image_np_with_annotations)

# Rubber Ducky data

We will start with some toy (literally) data consisting of 5 images of a rubber
ducky.  Note that the [coco](https://cocodataset.org/#explore) dataset contains a number of animals, but notably, it does *not* contain rubber duckies (or even ducks for that matter), so this is a novel class.

In [3]:
import glob

file_list = glob.glob("/media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/*.jpg")
#file_list = [file_list[0]]
#print("file_list: " + str(file_list))

# Load images and visualize
#train_image_dir = 'models/research/object_detection/test_images/ducky/train/'
train_image_dir = '/media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/'
train_images_np = []
train_images = [] 
for file in file_list:
  image_path = file
  print("file: " + str(file))
  train_images_np.append(load_image_into_numpy_array(image_path))
  train_images.append([file.split('/')[-1], load_image_into_numpy_array(image_path)])

plt.rcParams['axes.grid'] = False
plt.rcParams['xtick.labelsize'] = False
plt.rcParams['ytick.labelsize'] = False
plt.rcParams['xtick.top'] = False
plt.rcParams['xtick.bottom'] = False
plt.rcParams['ytick.left'] = False
plt.rcParams['ytick.right'] = False
plt.rcParams['figure.figsize'] = [14, 7]

#for idx, train_image_np in enumerate(train_images_np):
#  plt.subplot(4, 5, idx+1)
#  plt.imshow(train_image_np)
    
#plt.show()

file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/8ft_x_4ft_kids_matchday_soccer_goal.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/02.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/A1K2bZ2BwYjL._AC_SL1500_.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/23348-DEFAULT-l.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/01_Premier_Pro_Park__32068.1554316461.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/91aGo2a5uRL._AC_SL1500_.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/5ft_x_4ft_soccer_goal.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/1045264_1_large.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/41PyLd6g-2L.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/Big-Felt.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/1.jpg
file: /media/kimbring2/Steam/test_dataset_deepsoc

# Annotate images with bounding boxes

In this cell you will annotate the rubber duckies --- draw a box around the rubber ducky in each image; click `next image` to go to the next image and `submit` when there are no more images.

If you'd like to skip the manual annotation step, we totally understand.  In this case, simply skip this cell and run the next cell instead, where we've prepopulated the groundtruth with pre-annotated bounding boxes.



# In case you didn't want to label...

Run this cell only if you didn't annotate anything above and
would prefer to just use our preannotated boxes.  Don't forget
to uncomment.

In [ ]:
%matplotlib inline
from pycocotools.coco import COCO
import numpy as np
import skimage.io as io
import matplotlib.pyplot as plt
import pylab
import cv2 
import pickle as pkl

from data_aug.data_aug import *
from data_aug.bbox_util import *
pylab.rcParams['figure.figsize'] = (8.0, 10.0)

# initialize COCO api for instance annotations
annFile = '/media/kimbring2/Steam/test_dataset_deepsoccer/annotations.json'
coco = COCO(annFile)

cats = coco.loadCats(coco.getCatIds())

catIds = coco.getCatIds(catNms=['goal','goalpost']);
imgIds = coco.getImgIds(catIds=catIds);

print("len(imgIds): " + str(len(imgIds)))

len_original_image = len(train_images)

image_info_list = {}
for i in range(len_original_image):
    imgIds = coco.getImgIds(imgIds = [i])
    img = coco.loadImgs(imgIds[np.random.randint(0,len(imgIds))])[0]
    
    dataDir = '/media/kimbring2/Steam/test_dataset_deepsoccer'
    dataType = 'jpg'

    image_file_path = '%s/%s'%(dataDir, img['file_name'])
    I = io.imread(image_file_path)
    annIds = coco.getAnnIds(imgIds=img['id'], catIds=catIds, iscrowd=None)
    anns = coco.loadAnns(annIds)
    
    img_ = cv2.imread(image_file_path)
    bboxe = anns[0]['bbox']

    file_name = img['file_name'].split('/')[-1]
    
    width = img['width']
    height = img['height']
    
    category_id = anns[0]['category_id']
    
    bboxes = np.array([[bboxe[0], bboxe[1], (bboxe[0] + bboxe[2]), (bboxe[1] + bboxe[3])]], dtype=np.float32)
    gt_box = np.array([[bboxe[1] / height, bboxe[0] / width, (bboxe[1] + bboxe[3]) / height, (bboxe[0] + bboxe[2]) / width]], dtype=np.float32)
    image_info_list[file_name] = {"image": I, "bbox": bboxe, "size": [height, width], "class": category_id, "gt_box": gt_box}
    for j in range(0, 20):
        seq = Sequence([RandomHSV(40, 40, 30), RandomHorizontalFlip(), RandomScale(), RandomTranslate(), RandomRotate(10), RandomShear()])
        img__, bboxes_ = seq(img_.copy(), bboxes.copy())
        img__ = cv2.cvtColor(img__, cv2.COLOR_BGR2RGB)
        
        bboxes_original = [bboxes_[0][0], bboxes_[0][1], bboxes_[0][2] - bboxes_[0][0], bboxes_[0][3] -  bboxes_[0][1]]
        #print("bboxes_original: " + str(bboxes_original))

        # use url to load image
        #plotted_img = draw_rect(img__, bboxes_)
        #plt.imshow(plotted_img)
        #plt.show()
        
        # img['file_name']: JPEGImages/8ft_x_4ft_kids_matchday_soccer_goal.jpg
        new_file_name = img['file_name'].split('/')[-1]
        new_file_name = new_file_name.split('.')[-2]
        new_file_name = '%s_aug_%s.%s'%(new_file_name, j, 'jpg')
        #print("new_file_name: " + str(new_file_name))
        
        # load and display instance annotations
        gt_box = np.array([[bboxes_original[1] / height, bboxes_original[0] / width, (bboxes_original[1] + bboxes_original[3]) / height, (bboxes_original[0] + bboxes_original[2]) / width]], dtype=np.float32)
        image_info_list[new_file_name] = {"image": img__, "bbox": bboxes_original, "size": [img['height'], img['width']], "class": anns[0]['category_id'], "gt_box": gt_box}
    
#image_info_list

loading annotations into memory...
Done (t=0.00s)
creating index...
index created!
len(imgIds): 0


# Prepare data for training

Below we add the class annotations (for simplicity, we assume a single class in this colab; though it should be straightforward to extend this to handle multiple classes).  We also convert everything to the format that the training
loop below expects (e.g., everything converted to tensors, classes converted to one-hot representations, etc.).

In [6]:
# By convention, our non-background classes start counting at 1.  Given
# that we will be predicting just one class, we will therefore assign it a
# `class id` of 1.
#duck_class_id = 1
goal_class_id = 1
goalpost_class_id = 2
num_classes = 2

#category_index = {duck_class_id: {'id': duck_class_id, 'name': 'rubber_ducky'}}
category_index = {goal_class_id: {'id': goal_class_id, 'name': 'goal'},
                  goalpost_class_id: {'id': goalpost_class_id, 'name': 'goalpost'}}

# Convert class labels to one-hot; convert everything to tensors.
# The `label_id_offset` here shifts all classes by a certain number of indices;
# we do this here so that the model receives one-hot labels where non-background
# classes start counting at the zeroth index.  This is ordinarily just handled
# automatically in our training binaries, but we need to reproduce it here.
label_id_offset = 1
train_image_tensors = []
gt_classes_one_hot_tensors = []
gt_box_tensors = []
for image_info in image_info_list:
  #print(image_info_list[image_info]['image'])
  #print(image_info_list[image_info]['gt_box'])
  #print(image_info_list[image_info]['class'])

  #gt_boxes.append(image_info_list[image_info]['gt_box'])
  train_image_tensors.append(tf.expand_dims(tf.convert_to_tensor(image_info_list[image_info]['image'], dtype=tf.float32), axis=0))
  gt_box_tensors.append(tf.convert_to_tensor(image_info_list[image_info]['gt_box'], dtype=tf.float32))
  zero_indexed_groundtruth_classes = tf.convert_to_tensor(image_info_list[image_info]['class'] - label_id_offset)
  gt_classes_one_hot_tensors.append(tf.one_hot(zero_indexed_groundtruth_classes, num_classes))
    
print('Done prepping data.')

Done prepping data.


# Let's just visualize the rubber duckies as a sanity check


In [7]:
dummy_scores = np.array([1.0], dtype=np.float32)  # give boxes a score of 100%

plt.figure(figsize=(300, 150))
idx = 0
for image_info in image_info_list:
  #print(image_info_list[image_info]['image'])
  #print(image_info_list[image_info]['gt_box'])
  #print(image_info_list[image_info]['class'])
  plt.subplot(2, len(image_info_list) / 2 + 1, idx + 1)
  
  plot_detections(
      image_info_list[image_info]['image'],
      image_info_list[image_info]['gt_box'],
      np.ones(shape=[image_info_list[image_info]['gt_box'].shape[0]], dtype=np.int32),
      dummy_scores, category_index)
  idx += 1
plt.show()

# Create model and restore weights for all but last layer

In this cell we build a single stage detection architecture (RetinaNet) and restore all but the classification layer at the top (which will be automatically randomly initialized).

For simplicity, we have hardcoded a number of things in this colab for the specific RetinaNet architecture at hand (including assuming that the image size will always be 640x640), however it is not difficult to generalize to other model configurations.

In [8]:
# Download the checkpoint and put it into models/research/object_detection/test_data/

!wget http://download.tensorflow.org/models/object_detection/tf2/20200711/ssd_resnet50_v1_fpn_640x640_coco17_tpu-8.tar.gz
!tar -xf ssd_resnet50_v1_fpn_640x640_coco17_tpu-8.tar.gz
!mv ssd_resnet50_v1_fpn_640x640_coco17_tpu-8/checkpoint models/research/object_detection/test_data/

--2020-10-02 23:34:48--  http://download.tensorflow.org/models/object_detection/tf2/20200711/ssd_resnet50_v1_fpn_640x640_coco17_tpu-8.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 216.58.197.112, 2404:6800:4005:801::2010
접속 download.tensorflow.org (download.tensorflow.org)|216.58.197.112|:80... 접속됨.
HTTP request sent, awaiting response... 200 OK
Length: 244817203 (233M) [application/x-tar]
Saving to: ‘ssd_resnet50_v1_fpn_640x640_coco17_tpu-8.tar.gz.1’

ssd_resnet50_v1_fpn 100%[===================>] 233.48M  5.21MB/s    in 48s     

2020-10-02 23:35:37 (4.91 MB/s) - ‘ssd_resnet50_v1_fpn_640x640_coco17_tpu-8.tar.gz.1’ saved [244817203/244817203]

mv: 'ssd_resnet50_v1_fpn_640x640_coco17_tpu-8/checkpoint'를 'models/research/object_detection/test_data/'로 옮길 수 없음: 그런 파일이나 디렉터리가 없습니다


In [8]:
#tf.keras.backend.clear_session()

print('Building model and restoring weights for fine-tuning...', flush=True)
num_classes = 2
pipeline_config = '/media/kimbring2/Steam/models/research/object_detection/configs/tf2/ssd_resnet50_v1_fpn_640x640_coco17_tpu-8.config'
checkpoint_path = '/media/kimbring2/Steam/models/research/object_detection/test_data/checkpoint/ckpt-0'

# Load pipeline config and build a detection model.
#
# Since we are working off of a COCO architecture which predicts 90
# class slots by default, we override the `num_classes` field here to be just
# one (for our new rubber ducky class).
configs = config_util.get_configs_from_pipeline_file(pipeline_config)
model_config = configs['model']
model_config.ssd.num_classes = 2
model_config.ssd.freeze_batchnorm = True
detection_model = model_builder.build(model_config=model_config, is_training=True)

# Set up object-based checkpoint restore --- RetinaNet has two prediction
# `heads` --- one for classification, the other for box regression.  We will
# restore the box regression head but initialize the classification head
# from scratch (we show the omission below by commenting out the line that
# we would add if we wanted to restore both heads)
fake_box_predictor = tf.compat.v2.train.Checkpoint(
    _base_tower_layers_for_heads=detection_model._box_predictor._base_tower_layers_for_heads,
    # _prediction_heads=detection_model._box_predictor._prediction_heads,
    #    (i.e., the classification head that we *will not* restore)
    _box_prediction_head=detection_model._box_predictor._box_prediction_head,
    )

fake_model = tf.compat.v2.train.Checkpoint(
          _feature_extractor=detection_model._feature_extractor,
          _box_predictor=fake_box_predictor)

ckpt = tf.compat.v2.train.Checkpoint(model=fake_model)
ckpt.restore(checkpoint_path).expect_partial()

# Run model through a dummy image so that variables are created
image, shapes = detection_model.preprocess(tf.zeros([1, 640, 640, 3]))
prediction_dict = detection_model.predict(image, shapes)
_ = detection_model.postprocess(prediction_dict, shapes)
print('Weights restored!')

Building model and restoring weights for fine-tuning...
Weights restored!


# Eager mode custom training loop



In [10]:
tf.keras.backend.set_learning_phase(True)
#tf.compat.v1.disable_eager_execution()

# These parameters can be tuned; since our training set has 5 images
# it doesn't make sense to have a much larger batch size, though we could
# fit more examples in memory if we wanted to.
batch_size = 4
learning_rate = 0.01
num_batches = 2000

# Select variables in top layers to fine-tune.
trainable_variables = detection_model.trainable_variables
to_fine_tune = []
prefixes_to_train = [
  'WeightSharedConvolutionalBoxPredictor/WeightSharedConvolutionalBoxHead',
  'WeightSharedConvolutionalBoxPredictor/WeightSharedConvolutionalClassHead']


for var in trainable_variables:
  if any([var.name.startswith(prefix) for prefix in prefixes_to_train]):
    to_fine_tune.append(var)

    
# Set up forward + backward pass for a single train step.
def get_model_train_step_function(model, optimizer, vars_to_fine_tune):
  """Get a tf.function for training step."""

  # Use tf.function for a bit of speed.
  # Comment out the tf.function decorator if you want the inside of the
  # function to run eagerly.
  #@tf.function
  def train_step_fn(image_tensors,
                    groundtruth_boxes_list,
                    groundtruth_classes_list):
    """A single training iteration.

    Args:
      image_tensors: A list of [1, height, width, 3] Tensor of type tf.float32.
        Note that the height and width can vary across images, as they are
        reshaped within this function to be 640x640.
      groundtruth_boxes_list: A list of Tensors of shape [N_i, 4] with type
        tf.float32 representing groundtruth boxes for each image in the batch.
      groundtruth_classes_list: A list of Tensors of shape [N_i, num_classes]
        with type tf.float32 representing groundtruth boxes for each image in
        the batch.

    Returns:
      A scalar tensor representing the total loss for the input batch.
    """
    #print("groundtruth_boxes_list: " + str(groundtruth_boxes_list))
    shapes = tf.constant(batch_size * [[640, 640, 3]], dtype=tf.int32)
    model.provide_groundtruth(
        groundtruth_boxes_list=groundtruth_boxes_list,
        groundtruth_classes_list=groundtruth_classes_list)
    
    with tf.GradientTape() as tape:
      preprocessed_images = tf.concat([detection_model.preprocess(image_tensor)[0]
           for image_tensor in image_tensors], axis=0)
    
      #print("preprocessed_images.shape: " + str(preprocessed_images.shape))
      #plt.imshow(preprocessed_images[0])
      #plt.show()
    
      prediction_dict = model.predict(preprocessed_images, shapes)
      #print("prediction_dict: " + str(prediction_dict))
      losses_dict = model.loss(prediction_dict, shapes)
      #print("losses_dict['Loss/localization_loss']: " + str(losses_dict['Loss/localization_loss']))  
      #print("losses_dict['Loss/classification_loss']: " + str(losses_dict['Loss/classification_loss']))  
      
      total_loss = losses_dict['Loss/localization_loss'] + losses_dict['Loss/classification_loss']
      #total_loss = 0
      #print("total_loss: " + str(total_loss))
      gradients = tape.gradient(total_loss, vars_to_fine_tune)
      optimizer.apply_gradients(zip(gradients, vars_to_fine_tune))
        
    return total_loss

  return train_step_fn


optimizer = tf.keras.optimizers.SGD(learning_rate=learning_rate, momentum=0.9)
train_step_fn = get_model_train_step_function(detection_model, optimizer, to_fine_tune)

print('Start fine-tuning!', flush=True)
for idx in range(num_batches):
  # Grab keys for a random subset of examples
  all_keys = list(range(len(train_images_np)))
  random.shuffle(all_keys)
  example_keys = all_keys[:batch_size]

  # Note that we do not do data augmentation in this demo.  If you want a
  # a fun exercise, we recommend experimenting with random horizontal flipping
  # and random cropping :)
  gt_boxes_list = [gt_box_tensors[key] for key in example_keys]
  gt_classes_list = [tf.reshape(gt_classes_one_hot_tensors[key], [1, 2]) for key in example_keys]
  image_tensors = [train_image_tensors[key] for key in example_keys]

  #print("gt_boxes_list[0].shape: " + str(gt_boxes_list[0].shape))
  #print("image_tensors[0].shape: " + str(image_tensors[0].shape))
  #plt.imshow(image_tensors[0][0].numpy().astype(np.int32))
  #plt.show()
    
  #print("gt_classes_list: " + str(gt_classes_list))
  # Training step (forward pass + backwards pass)
  total_loss = train_step_fn(image_tensors, gt_boxes_list, gt_classes_list)
  tf.keras.backend.clear_session()
    
  if idx % 10 == 0:
    print('batch ' + str(idx) + ' of ' + str(num_batches)
    + ', loss=' +  str(total_loss.numpy()), flush=True)

print('Done fine-tuning!')

Start fine-tuning!


ResourceExhaustedError: OOM when allocating tensor with shape[1,800,800,3] and type float on /job:localhost/replica:0/task:0/device:GPU:0 by allocator GPU_0_bfc [Op:Sub] name: Preprocessor/sub/

# Load test images and run inference with new model!

In [20]:
#file_list = glob.glob("/home/kimbring2/Desktop/tennis_ball/*.jpg")
#file_list = glob.glob("/media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/*.jpg")
file_list = glob.glob("/home/kimbring2/Desktop/content_image/*.jpg")
#file_list = [file_list[0]]
#print("file_list: " + str(file_list))

# Load images and visualize
#train_image_dir = 'models/research/object_detection/test_images/ducky/train/'
train_image_dir = '/media/kimbring2/Steam/test_dataset_deepsoccer/JPEGImages/'

test_image_dir = 'models/research/object_detection/test_images/ducky/test/'
test_images_np = []
#for i in range(1, 50):
for file in file_list:
  #image_path = os.path.join(test_image_dir, 'out' + str(i) + '.jpg')
  image_path = file
  #print("image_path: " + str(image_path))
  test_images_np.append(np.expand_dims(load_image_into_numpy_array(image_path), axis=0))


# Again, uncomment this decorator if you want to run inference eagerly
@tf.function
def detect(input_tensor):
  """Run detection on an input image.

  Args:
    input_tensor: A [1, height, width, 3] Tensor of type tf.float32.
      Note that height and width can be anything since the image will be
      immediately resized according to the needs of the model within this
      function.

  Returns:
    A dict containing 3 Tensors (`detection_boxes`, `detection_classes`,
      and `detection_scores`).
  """
  preprocessed_image, shapes = detection_model.preprocess(input_tensor)
  #print("shapes: " + str(shapes))
  prediction_dict = detection_model.predict(preprocessed_image, shapes)

  return detection_model.postprocess(prediction_dict, shapes)


# Note that the first frame will trigger tracing of the tf.function, which will
# take some time, after which inference should be fast.
label_id_offset = 1
for i in range(len(test_images_np)):
  input_tensor = tf.convert_to_tensor(test_images_np[i], dtype=tf.float32)
  detections = detect(input_tensor)
  #print("detections: " + str(detections))
    
  plot_detections(
      test_images_np[i][0],
      detections['detection_boxes'][0].numpy(),
      detections['detection_classes'][0].numpy().astype(np.uint32)+ label_id_offset,
      detections['detection_scores'][0].numpy(),
      category_index, figsize=(15, 20), image_name="gif_frame_" + ('%02d' % i) + ".jpg")

In [ ]:
imageio.plugins.freeimage.download()

#anim_file = 'duckies_test.gif'
anim_file = 'deepsoccer_test.gif'

filenames = glob.glob('gif_frame_*.jpg')
filenames = sorted(filenames)
last = -1
images = []
for filename in filenames:
  image = imageio.imread(filename)
  images.append(image)

imageio.mimsave(anim_file, images, 'GIF-FI', fps=5)

display(IPyImage(open(anim_file, 'rb').read()))